### Exercise 57

#### Import

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import norm, uniform, lognorm, poisson, gamma
from scipy.special import gamma as gammafunc
from scipy.stats import gaussian_kde as kde

#### Data

In [2]:
y = np.array([6, 8, 7, 6, 7, 4, 11, 8, 6, 3])
n = len(y)

#### Parameters

In [3]:
S = 10_000

# Plotting
mplot = 200
space = np.linspace(2, 10, mplot)

#### Functions

In [4]:
def get_log_likelihood(theta):
    return np.sum(poisson(theta).logpmf(y))


def get_MH_sample(S, sigma, prior):
    sample = np.zeros(S)
    
    for s in range(S):
        if s == 0:
            sample[s] = prior.rvs()
            continue
        
        else:
            current = sample[s - 1]
            proposed = sample[s - 1] + sigma*norm().rvs()
            
            if proposed < 0:
                sample[s] = current
                continue
            
            logprior_current = prior.logpdf(current)
            logprior_proposed = prior.logpdf(proposed)
            
            loglik_current = get_log_likelihood(current)
            loglik_proposed = get_log_likelihood(proposed)
            
            log_acceptance_prob = logprior_proposed + loglik_proposed - logprior_current - loglik_current
            
            U = np.random.random()
            
            if np.log(U) < log_acceptance_prob:
                sample[s] = proposed
            else:
                sample[s] = current
    return sample

#### (a)

In [5]:
# Specify prior
a, b = .1, .1
prior = gamma(a=a, scale=1/b)

# Run algorithm
sample = get_MH_sample(S, 1.0, prior)

In [6]:
# Plots
plt.plot(space, kde(sample)(space), color='black', label='MCMC')
plt.plot(space, gamma(a=a + np.sum(y), scale=1/(b + n)).pdf(space), 
         color='black', linestyle='dashed', label='exact')
plt.legend()
plt.xlabel('theta')
plt.ylabel('posterior density')
plt.show()

In [7]:
# Trace plots
plt.plot(np.arange(S), sample, color='black')
plt.xlabel('iteration')
plt.ylabel('theta')
plt.show()

#### (b)

In [8]:
# Specify prior
a, b = .5, 50
prior = uniform(loc=a, scale=b - a)

# Run algorithm
sample = get_MH_sample(S, 1.0, prior)

# Exact
ybar = np.mean(y)
I = gamma(a=1 + n*ybar, scale=1/n).cdf(b) - gamma(a=1 + n*ybar, scale=1/n).cdf(a)
posterior = n**(1 + n*ybar)/(gammafunc(1 + n*ybar)) * space**(n*ybar) * np.exp(-n*space) / I

In [9]:
# Plots
plt.plot(space, kde(sample)(space), color='black', label='MCMC')
plt.plot(space, posterior, color='black', linestyle='dashed', label='exact')
plt.legend()
plt.xlabel('theta')
plt.ylabel('posterior density')
plt.show()

#### (c)

In [10]:
# Specify prior
prior = lognorm(1)

# Run algorithm
sample = get_MH_sample(S, 1.0, prior)

In [11]:
# Plots
plt.plot(space, kde(sample)(space), color='black', label='MCMC')
plt.legend()
plt.xlabel('theta')
plt.ylabel('posterior density')
plt.show()